# Laden der Rohdaten

In [1]:
import pickle

# Laden der 'kirp' Liste aus der Pickle-Datei
with open('rick.pickle', 'rb') as f:
    data_frame = pickle.load(f)

# PCA Klasse zu Reduktion der Dimensionen

In [2]:
from torch.utils.data import Dataset
import torch
import pandas as pd
from sklearn.preprocessing import LabelEncoder
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from typing import List, Tuple


class SplittedDataset(Dataset):
    def __init__(self, dataframe):
        self.dataframe = dataframe
        self.genome_frequencies = torch.tensor(dataframe['pca_frequencies'].tolist(), dtype=torch.float32)
        self.cancer_types = torch.tensor(dataframe['encoded_cancer_type'].tolist(), dtype=torch.long)

    def __getitem__(self, index):
        return self.genome_frequencies[index], self.cancer_types[index]

    def __len__(self):
        return len(self.dataframe)


class GenomeDataset(Dataset):
    """
    Eine benutzerdefinierte Dataset-Klasse, die für die Handhabung von Genomdaten konzipiert ist.
    Diese Klasse wendet eine Principal Component Analysis (PCA) auf die Frequenzen der Genome an
    und teilt den Datensatz in Trainings- und Validierungsteile auf.

    Attributes:
        dataframe (pd.DataFrame): Ein Pandas DataFrame, der die initialen Daten enthält.
        train_df (pd.DataFrame): Ein DataFrame, der den Trainingsdatensatz nach der Anwendung von PCA und der Aufteilung enthält.
        val_df (pd.DataFrame): Ein DataFrame, der den Validierungsdatensatz nach der Anwendung von PCA und der Aufteilung enthält.

    Methods:
        __init__(self, dataframe, n_pca_components=1034, train_size=0.8, split_random_state=42):
            Konstruktor für die GenomeDataset Klasse.
        _do_PCA(self, frequencies, n_components=1034):
            Wendet PCA auf die gegebenen Frequenzen an.
        _split_dataset(self, train_size=0.8, random_state=42):
            Teilt den DataFrame in Trainings- und Validierungsdatensätze auf.
        __getitem__(self, index):
            Gibt ein Tupel aus transformierten Frequenzen und dem zugehörigen Krebstyp für einen gegebenen Index zurück.
        __len__(self):
            Gibt die Gesamtlänge der kombinierten Trainings- und Validierungsdatensätze zurück.
    """

    def __init__(self, dataframe: pd.DataFrame, n_pca_components: int = 1034, train_size: float = 0.8, split_random_state: int = 42):
        """
        Konstruktor für die GenomeDataset Klasse.

        Parameters:
            dataframe (pd.DataFrame): Der DataFrame, der die Genome Frequenzen und Krebsarten enthält.
            n_pca_components (int): Die Anzahl der PCA-Komponenten, auf die reduziert werden soll. Standardwert ist 1034.
            train_size (float): Der Anteil der Daten, der als Trainingsdaten verwendet werden soll. Standardwert ist 0.8.
            split_random_state (int): Der Zufalls-Saatwert, der für die Aufteilung des Datensatzes verwendet wird. Standardwert ist 42.
        """
        self.dataframe = dataframe

        # Umwandlung der Krebsarten in numerische Werte
        self.label_encoder = LabelEncoder()
        self.dataframe['encoded_cancer_type'] = self.label_encoder.fit_transform(dataframe['cancer_type'])

        # Anwenden der PCA auf die Frequenzen
        self.dataframe['pca_frequencies'] = self._do_PCA(self.dataframe['genome_frequencies'].tolist(), n_pca_components)

        # Teilen des DataFrame in Trainings- und Validierungsdatensatz
        self._split_dataset(train_size=train_size, random_state=split_random_state)

    def transform_datapoint(self, datapoint: List[float]) -> List[float]:
        """
        Transformiert einen einzelnen Datenpunkt durch Standardisierung und Anwendung der PCA.

        Diese Methode nimmt einen rohen Datenpunkt (eine Liste von Frequenzen), standardisiert ihn mit dem 
        zuvor angepassten Scaler und wendet dann die PCA-Transformation an, um ihn in den reduzierten 
        Feature-Raum zu überführen, der für das Training des Modells verwendet wurde.

        Parameters:
            datapoint (List[float]): Ein roher Datenpunkt, bestehend aus einer Liste von Frequenzen.

        Returns:
            List[float]: Der transformierte Datenpunkt, nach Anwendung der Standardisierung und der PCA.
        """
        # Standardisierung des Datenpunkts
        scaled_data_point = self.scaler.transform([datapoint])

        # PCA-Transformation des standardisierten Datenpunkts
        pca_transformed_point = self.pca.transform(scaled_data_point)

        return pca_transformed_point.tolist()

    def _do_PCA(self, frequencies: List[List[float]], n_components: int = 1034) -> List[List[float]]:
        """
        Wendet PCA auf die gegebenen Frequenzen an.

        Parameters:
            frequencies (List[List[float]]): Die Liste der Frequenzen, auf die die PCA angewendet werden soll.
            n_components (int): Die Anzahl der Komponenten für die PCA. Standardwert ist 1034.

        Returns:
            List[List[float]]: Eine Liste von Listen, die die transformierten Frequenzen nach der PCA darstellt.
        """

        # Standardisieren der Frequenzen
        self.scaler = StandardScaler()
        scaled_frequencies = self.scaler.fit_transform(frequencies)

        # PCA-Instanz erstellen und auf die gewünschte Anzahl von Komponenten reduzieren
        self.pca = PCA(n_components=n_components)

        # PCA auf die Frequenzen anwenden
        pca_result = self.pca.fit_transform(scaled_frequencies)

        return pca_result.tolist()

    def _split_dataset(self, train_size: float = 0.8, random_state: int = 42):
        """
        Teilt den DataFrame in Trainings- und Validierungsdatensätze auf.

        Parameters:
            train_size (float): Der Anteil der Daten, der als Trainingsdaten verwendet werden soll.
            random_state (int): Der Zufalls-Saatwert, der für die Aufteilung des Datensatzes verwendet wird.
        """

        # Teilen des DataFrame in Trainings- und Validierungsdatensatz
        train_df, val_df = train_test_split(self.dataframe, train_size=train_size, random_state=random_state)
        self.train_df = SplittedDataset(train_df)
        self.val_df = SplittedDataset(val_df)


    def __getitem__(self, index: int) -> Tuple[torch.Tensor, int]:
        """
        Gibt ein Tupel aus transformierten Frequenzen und dem entsprechenden Krebstyp für einen gegebenen Index zurück.

        Parameters:
            index (int): Der Index des zu abrufenden Datenelements.

        Returns:
            Tuple[torch.Tensor, int]: Ein Tupel, bestehend aus einem Tensor der transformierten Frequenzen und dem zugehörigen Krebstyp.
        """

        print(self.train_df.shape)
        print(self.val_df.shape)
        
        if index < len(self.train_df):
            row = self.train_df.iloc[index]
        else:
            row = self.val_df.iloc[len(self.train_df) - index]

        pca_frequencies_tensor = torch.tensor(row['pca_frequencies'], dtype=torch.float32)
        cancer_type = row['encoded_cancer_type']

        return pca_frequencies_tensor, cancer_type

    def __len__(self) -> int:
        """
        Gibt die Gesamtlänge der kombinierten Trainings- und Validierungsdatensätze zurück.

        Returns:
            int: Die Länge der kombinierten Datensätze.
        """
        
        return len(self.train_df) + len(self.val_df)


# Definition des neuronalen Netzes

In [3]:
from torch.utils.data import DataLoader
from multiprocessing import cpu_count
import os
import neat
import numpy as np

class CancerClassifierNEAT():
    def __init__(self, dataframe: pd.DataFrame, n_pca_components: int = 64) -> None:
        self.num_generations = None
        self.n_pca_components = n_pca_components
        # Initialisierung der config Datei
        local_dir = os.getcwd()
        config_path = os.path.join(local_dir, 'config')
        config = neat.Config(neat.DefaultGenome, neat.DefaultReproduction, neat.DefaultSpeciesSet, neat.DefaultStagnation, config_path)
        # Initialisierung der Population
        self.pop = neat.Population(config)
        stats = neat.StatisticsReporter()
        self.pop.add_reporter(stats)
        self.pop.add_reporter(neat.StdOutReporter(True))
        # Erstellen des Datensatzes
        genome_dataset = GenomeDataset(data_frame, n_pca_components=n_pca_components)
        self.train_dataset = genome_dataset.train_df
        self.valid_dataset = genome_dataset.val_df
        # Erstellen der Datensatzloader
        self.train_loader = DataLoader(dataset=self.train_dataset, batch_size=1, shuffle=True)
        self.valid_loader = DataLoader(dataset=self.valid_dataset, batch_size=1, shuffle=False)

        self.training_accuracies = []
        self.validation_accuracies = []

    def fitness(self, genome: neat.DefaultGenome, config) -> float:
        net = neat.nn.FeedForwardNetwork.create(genome, config)

        correct_predictions = 0
        total_predictions = 0

        for i, (inputs, labels) in enumerate(self.train_loader):
            inputs_list = inputs.view(-1).tolist()
            #print(inputs_list)
            # Netz aktivieren
            outputs = net.activate(inputs_list)
            #print(outputs)
            # Berechnen der Genauigkeit
            predicted = np.argmax(np.array(outputs))
            correct_predictions += (predicted == labels).sum().item()
            total_predictions += labels.size(0)

        train_accuracy = correct_predictions / total_predictions

        return train_accuracy

    def eval_genomes(self, genomes, config):
        for _, genome in genomes:
            genome.fitness = self.fitness(genome, config)

    def run(self, num_generations: int = 500) -> neat.DefaultGenome:
        #parallel = neat.ParallelEvaluator(cpu_count(), self.fitness)
        #winner = self.pop.run(parallel.evaluate, num_generations)
        winner = self.pop.run(self.eval_genomes, num_generations)

        return winner

In [5]:
ea = CancerClassifierNEAT(data_frame)
ea.run()


 ****** Running generation 0 ****** 

Population's average fitness: 0.31162 stdev: 0.16467
Best fitness: 0.68803 - size: (13, 431) - species 47 - id 47
Average adjusted fitness: 0.216
Mean genetic distance 3.635, standard deviation 0.325
Population of 500 members in 100 species:
   ID   age  size  fitness  adj fit  stag
  ====  ===  ====  =======  =======  ====
     1    0     5      0.3    0.213     0
     2    0     5      0.4    0.294     0
     3    0     5      0.3    0.189     0
     4    0     5      0.1    0.005     0
     5    0     5      0.4    0.299     0
     6    0     5      0.3    0.210     0
     7    0     5      0.4    0.326     0
     8    0     5      0.2    0.125     0
     9    0     5      0.6    0.463     0
    10    0     5      0.2    0.149     0
    11    0     5      0.2    0.134     0
    12    0     5      0.5    0.447     0
    13    0     5      0.6    0.497     0
    14    0     5      0.6    0.489     0
    15    0     5      0.3    0.213     0
    1

KeyboardInterrupt: 

In [ ]:
from IPython.display import clear_output
import matplotlib.pyplot as plt

# Listen, um Verluste zu speichern
train_losses = []
valid_losses = []
train_accuracies = []
valid_accuracies = []

for epoch in range(num_epochs):
    model.train()
    train_loss = 0.0
    correct_predictions = 0
    total_predictions = 0

    for i, (inputs, labels) in enumerate(train_loader):
        inputs, labels = inputs.to(device), labels.to(device)
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()
        train_loss += loss.item()

        # Berechnen der Genauigkeit
        _, predicted = torch.max(outputs, 1)
        correct_predictions += (predicted == labels).sum().item()
        total_predictions += labels.size(0)

    # Durchschnittlicher Trainingsverlust und Genauigkeit
    train_loss /= len(train_loader)
    train_accuracy = correct_predictions / total_predictions
    train_losses.append(train_loss)
    train_accuracies.append(train_accuracy)

    # Validierungsverlust und Genauigkeit
    model.eval()
    valid_loss = 0.0
    correct_predictions = 0
    total_predictions = 0

    with torch.no_grad():
        for inputs, labels in valid_loader:
            inputs, labels = inputs.to(device), labels.to(device)
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            valid_loss += loss.item()

            # Berechnen der Genauigkeit
            _, predicted = torch.max(outputs, 1)
            correct_predictions += (predicted == labels).sum().item()
            total_predictions += labels.size(0)

    # Durchschnittlicher Validierungsverlust und Genauigkeit
    valid_loss /= len(valid_loader)
    valid_accuracy = correct_predictions / total_predictions
    valid_losses.append(valid_loss)
    valid_accuracies.append(valid_accuracy)


    # Aktualisieren des Graphen
    clear_output(wait=True)
    fig, ax1 = plt.subplots()

    # Zeichnen der Verlustkurven
    ax1.plot(train_losses, label='Trainingsverlust', color='r')
    ax1.plot(valid_losses, label='Validierungsverlust', color='b')
    ax1.set_xlabel('Epochen')
    ax1.set_ylabel('Verlust', color='g')
    ax1.tick_params(axis='y', labelcolor='g')

    # Zweite y-Achse für die Genauigkeit
    ax2 = ax1.twinx()
    ax2.plot(train_accuracies, label='Trainingsgenauigkeit', color='r', linestyle='dashed')
    ax2.plot(valid_accuracies, label='Validierungsgenauigkeit', color='b', linestyle='dashed')
    ax2.set_ylabel('Genauigkeit', color='g')
    ax2.tick_params(axis='y', labelcolor='g')

    # Titel und Legende
    plt.title('Trainings- und Validierungsverlust und -genauigkeit über die Zeit')
    fig.tight_layout()
    ax1.legend(loc='lower left')
    ax2.legend(loc='lower right')

    plt.show()

    print(f'Epoch [{epoch+1}/{num_epochs}], Trainingsverlust: {train_loss:.4f}, Validierungsverlust: {valid_loss:.4f}')